In [7]:
import numpy as np
import plotly.graph_objects as go
import plotly.express as px
import json
import os
import pandas as pd


folder = 'results1/onenet_ETTm2_pl24_olfull_optadam_tb1_2025_08_24_04_16_fc33'
feature = 0
trial = 1

mae_cumul = np.load(folder + '/mae.npy')
mse_cumul = np.load(folder + '/mse.npy')
metrics = np.load(folder + '/metrics.npy')
preds = np.load(folder + '/preds.npy')
trues = np.load(folder + '/trues.npy')
with open(folder + '/args.json') as f:
    args = json.load(f)

print('lr: ', args['online_lr'], 'regul ', args['OCAR_regul'], 'regul_last', args['OCAR_regul_last'])

print('MAE: ', metrics[trial, 0], ' MSE: ', metrics[trial, 1]) 
print(metrics)


fig = go.Figure()
fig.add_trace(go.Scatter(x=np.arange(len(mae_cumul[trial])), y=mae_cumul[trial], mode='lines', name='MAE'))
fig.add_trace(go.Scatter(x=np.arange(len(mse_cumul[trial])), y=mse_cumul[trial], mode='lines', name='MSE'))
fig.show()

fig = go.Figure()
fig.add_trace(go.Scatter(x=np.arange(len(preds[trial, :, feature])), y=preds[trial, :, feature], mode='lines', name='Predictions'))
fig.add_trace(go.Scatter(x=np.arange(len(trues[trial, :, feature])), y=trues[trial, :, feature], mode='lines', name='True'))
fig.show()

max = 0
feat = 0
for i in range(preds.shape[2]):
    mse = np.mean((preds[trial, :, i] - trues[trial, :, i]) ** 2)
    if mse > max:
        max = mse
        feat = i
print('Max MSE: ', max, ' for feature ', feat)
fig = go.Figure()
fig.add_trace(go.Scatter(x=np.arange(len(preds[trial, :, feat])), y=preds[trial, :, feat], mode='lines', name='Predictions'))
fig.add_trace(go.Scatter(x=np.arange(len(trues[trial, :, feat])), y=trues[trial, :, feat], mode='lines', name='True'))
fig.show()

    

    






lr:  0.000105460875348624 regul  0.1 regul_last 0.1
MAE:  0.417095851553076  MSE:  0.4579861554119885
[[4.17145645e-01 4.54538782e-01 6.40953073e-01 1.02402034e+00
  3.51538056e+01 4.34932934e+02]
 [4.17095852e-01 4.57986155e-01 6.41595038e-01 1.02488753e+00
  3.47337878e+01 4.53927788e+02]
 [4.22956087e-01 4.69890486e-01 6.51246442e-01 1.02216154e+00
  3.46452283e+01 4.48978691e+02]]


Max MSE:  2.655709  for feature  166


In [ ]:
import os
import json
import numpy as np
import pandas as pd
import datetime
# Base results directory
BASE_DIR = 'results1_hpo_etth1_5runs copy'
i = 3

# %% [markdown]
# ## 2. Collect all records

# %%
records = []

# iterate subdirectories
for root, dirs, files in os.walk(BASE_DIR):
    if 'args.json' in files and 'metrics.npy' in files:
        # 1. parse the folder basename
        folder = os.path.basename(root)
        parts = folder.split('_')
        # assume last 6 parts are [YYYY,MM,DD,HH,MM,<run_id>]
        date_str = '_'.join(parts[-6:-1])
        timestamp = datetime.datetime.strptime(date_str, '%Y_%m_%d_%H_%M')
        
        # 2. load args & metrics
        with open(os.path.join(root, 'args.json'), 'r') as f:
            args = json.load(f)
        metrics = np.load(os.path.join(root, 'metrics.npy'))
        mae = metrics[:i, 0].mean()
        mae_sd = metrics[:i, 0].std()
        exp_time = metrics[:i, 5].mean()

        if len(metrics[:i, 0]) != len(set(metrics[:i, 0])):
            print(f"Warning: Duplicate MAE values found in {root}.")

        #Load predictions and true values 
        preds = np.load(os.path.join(root, 'preds.npy'))
        trues = np.load(os.path.join(root, 'trues.npy'))   

        #Compute the MAE of the naive predictor (predicting the last observed value)
        naive_mae = np.mean(np.abs(trues[:i] - np.roll(trues[:i], shift=1, axis=1)))
        mase = metrics[:i, 0] / naive_mae
        mase_sd = mase.std()
        mase = mase.mean()

        
        # 3. build record, including the parsed timestamp
        rec = {
            'method':          args.get('method'),
            'data':            args.get('data'),
            'online_lr':    args.get('online_lr'),
            'deg_f':           args.get('deg_f'),
            'MASE':             mase,
            'MASE_sd':             mase_sd,
            'run_timestamp':   timestamp,              # new
            'run_date':        timestamp.date(),        # if you only care about the date
            'exp_time':        exp_time
        }
        records.append(rec)
# 4. DataFrame
df = pd.DataFrame.from_records(records)

# 5. Pivot including the date
table = df.pivot_table(
    index=['method',  'online_lr', 'deg_f'],
    columns='data',
    values=['MASE', 'MASE_sd', 'exp_time'],
).sort_index()

display(table)


MASE                                \
data                                  ECL     ETTh1     ETTh2     ETTm1   
method          online_lr deg_f                                           
derpp           0.000100  50.0   2.885953  1.448083  1.595878  1.825777   
                          500.0       NaN       NaN       NaN       NaN   
er              0.000196  50.0   3.208304  1.490157  1.595596  1.815686   
                          500.0       NaN       NaN       NaN       NaN   
fsnet           0.000182  500.0  2.989976  1.053351  1.355996  1.391215   
ocar_derpp_temp 0.064362  500.0  1.606671  0.925853       NaN  1.104918   
                0.095081  50.0   3.741540  0.912278       NaN  1.096714   
ocar_fsnet_temp 0.000179  500.0  5.140313  1.012477  1.767359  1.340383   
                0.000202  50.0   3.672395  0.992052  1.612279  1.338448   
ocar_temp       0.000124  500.0  1.537823  1.418732  1.748105  1.902095   
                0.085683  50.0   3.777828  0.935457  1.287738  1.096599   
ogd             0.000115  50.0   3.124200  1.495472  1.650677  2.193700   
                          500.0       NaN       NaN       NaN       NaN   
onenet          0.000105  50.0   1.137423  1.417165  1.522574  1.855019   
                          500.0       NaN       NaN       NaN       NaN   

                                                                         \
data                                ETTm2       Toy      ToyG   Traffic   
method          online_lr deg_f                                           
derpp           0.000100  50.0        NaN  0.923708  0.927014  0.944908   
                          500.0  1.807200       NaN       NaN       NaN   
er              0.000196  50.0        NaN  0.923485  0.927939  1.065876   
                          500.0  1.796956       NaN       NaN       NaN   
fsnet           0.000182  500.0  1.464296  0.797263  0.813094  0.951878   
ocar_derpp_temp 0.064362  500.0       NaN  0.893847  0.898723  1.059710   
                0.095081  50.0        NaN  0.873412  0.887981  0.973817   
ocar_fsnet_temp 0.000179  500.0       NaN  0.780595  0.792621  0.956778   
                0.000202  50.0        NaN  0.774886  0.791928  0.907134   
ocar_temp       0.000124  500.0  1.864786  0.924639  0.929550  0.876724   
                0.085683  50.0   1.294678  0.877680  0.890092  0.997169   
ogd             0.000115  50.0        NaN  0.923648  0.926717  1.047547   
                          500.0  2.025431       NaN       NaN       NaN   
onenet          0.000105  50.0        NaN  0.921777  0.926894  0.970481   
                          500.0  1.803620       NaN       NaN       NaN   

                                            MASE_sd                      \
data                                  WTH       ECL     ETTh1     ETTh2   
method          online_lr deg_f                                           
derpp           0.000100  50.0   1.834489  0.008621  0.012961  0.005252   
                          500.0       NaN       NaN       NaN       NaN   
er              0.000196  50.0   1.895599  0.019564  0.014364  0.004081   
                          500.0       NaN       NaN       NaN       NaN   
fsnet           0.000182  500.0  1.390714  0.022614  0.008844  0.006614   
ocar_derpp_temp 0.064362  500.0  1.216633  0.059966  0.004743       NaN   
                0.095081  50.0   1.172325  0.003709  0.003622       NaN   
ocar_fsnet_temp 0.000179  500.0  1.285378  0.318698  0.030835  0.111745   
                0.000202  50.0   1.245515  0.013769  0.024419  0.061825   
ocar_temp       0.000124  500.0  1.841578  0.013712  0.001257  0.048779   
                0.085683  50.0   1.183383  0.004268  0.006366  0.038887   
ogd             0.000115  50.0   1.982550  0.025232  0.013147  0.014436   
                          500.0       NaN       NaN       NaN       NaN   
onenet          0.000105  50.0   1.797603  0.006010  0.010536  0.008002   
                          500.0       NaN       NaN       Na

In [ ]:
import pandas as pd
import matplotlib.pyplot as plt

df_complete = pd.read_csv('grad_norm_history.csv')

for k in [0.001, 0.1, 1]:
    j = 1
    i = 5
    df = df_complete[(df_complete['deg_f'] == i) & (df_complete['scale'] == j ) & (df_complete['regul'] == k)]

    #Do the same plot with plotly
    import plotly.express as px
    import plotly.graph_objects as go
    fig = go.Figure()
    fig.add_trace(go.Scatter(x=df['input_norm'], y=df['regularized_grad_norm'], mode='markers', name='Natural Gradient'))
    fig.add_trace(go.Scatter(x=df['input_norm'], y=df['original_grad_norm'], mode='markers', name='Original Gradient'))
    fig.update_xaxes(type="log")
    fig.update_yaxes(type="log")
    fig.update_layout(
                        xaxis_title='Input Norm',
                        yaxis_title='Gradient Norm',
                        title='Gradient Norms for ' + str(i))
    fig.show()

    fig = go.Figure()
    fig.add_trace(go.Scatter(x=df['target_norm'], y=df['regularized_grad_norm'], mode='markers', name='Natural Gradient'))
    fig.add_trace(go.Scatter(x=df['target_norm'], y=df['original_grad_norm'], mode='markers', name='Original Gradient'))
    fig.update_xaxes(type="log")
    fig.update_yaxes(type="log")
    fig.update_layout(
                        xaxis_title='Error Norm',
                        yaxis_title='Gradient Norm',
                        title='Gradient Norms for ' + str(i))
    fig.show()


fig = go.Figure()
for i in [5, 10, 20]:
    j = 1
    k = 0.001
    df = df_complete[(df_complete['deg_f'] == i) & (df_complete['scale'] == j ) & (df_complete['regul'] == k)]
    df2 = df.sort_values(by=['target_norm'])
    fig.add_trace(go.Scatter(x=df2['target_norm'], y=df2['regularized_grad_norm'].rolling(window=100).mean(), mode='lines', name='deg_f ' + str(i)))
    fig.update_xaxes(type="log")
fig.show()

fig = go.Figure()
for j in [0.1, 1, 10]:
    i = 5
    k = 0.001
    df = df_complete[(df_complete['deg_f'] == i) & (df_complete['scale'] == j ) & (df_complete['regul'] == k)]
    df2 = df.sort_values(by=['target_norm'])
    fig.add_trace(go.Scatter(x=df2['target_norm'], y=df2['regularized_grad_norm'].rolling(window=100).mean(), mode='lines', name='scale' + str(j)))
    fig.update_xaxes(type="log")
fig.show()

fig = go.Figure()
for k in [0.001, 0.1, 1]:
    j = 1
    i = 5
    df = df_complete[(df_complete['deg_f'] == i) & (df_complete['scale'] == j ) & (df_complete['regul'] == k)]
    df2 = df.sort_values(by=['target_norm'])
    fig.add_trace(go.Scatter(x=df2['target_norm'], y=df2['regularized_grad_norm'].rolling(window=100).mean(), mode='lines', name='regul ' + str(k)))
    fig.update_xaxes(type="log")
fig.show()

#########################
fig = go.Figure()
for i in [5, 10, 20]:
    j = 1
    k = 0.001
    df = df_complete[(df_complete['deg_f'] == i) & (df_complete['scale'] == j ) & (df_complete['regul'] == k)]
    df2 = df.sort_values(by=['input_norm'])
    fig.add_trace(go.Scatter(x=df2['input_norm'], y=df2['regularized_grad_norm'].rolling(window=100).mean(), mode='lines', name='deg_f ' + str(i)))
    fig.update_xaxes(type="log")
fig.show()

fig = go.Figure()
for j in [0.1, 1, 10]:
    i = 5
    k = 0.001
    df = df_complete[(df_complete['deg_f'] == i) & (df_complete['scale'] == j ) & (df_complete['regul'] == k)]
    df2 = df.sort_values(by=['input_norm'])
    fig.add_trace(go.Scatter(x=df2['input_norm'], y=df2['regularized_grad_norm'].rolling(window=100).mean(), mode='lines', name='scale' + str(j)))
    fig.update_xaxes(type="log")
fig.show()

fig = go.Figure()
for k in [0.001, 0.1, 1]:
    j = 1
    i = 5
    df = df_complete[(df_complete['deg_f'] == i) & (df_complete['scale'] == j ) & (df_complete['regul'] == k)]
    df2 = df.sort_values(by=['input_norm'])
    fig.add_trace(go.Scatter(x=df2['input_norm'], y=df2['regularized_grad_norm'].rolling(window=100).mean(), mode='lines', name='regul ' + str(k)))
    fig.update_xaxes(type="log")
fig.show()


